In [ ]:
<style>div.prompt {display:none}</style>

# Cambios en el consumo a nivel local

In [1]:
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import seaborn as sns

from datetime import datetime, timedelta
from folium import Map, LayerControl, GeoJson, GeoJsonTooltip

from helper_functions import custom_dual_map, plot_dual_map

Fuentes de datos:

* *Códigos Postales de la Ciudad de México*, información geográfica en formato GeoJSON:  https://datos.cdmx.gob.mx/dataset/codigos-postales

:::{warning}
Try changing `tip` to `warning`!
:::

In [2]:
df = pd.read_csv('unscaled_data.csv')
df['date'] = pd.to_datetime(df['date'])
df['zip_code'] = df['zip_code'].astype(str).apply(lambda x: x.zfill(5))
df = df[['date', 'hour'] + [c for c in df.columns if c not in ('date', 'hour')]].drop(columns=['transaction_online', 'transaction_physical'])

In [3]:
df.describe(exclude=['datetime', 'int'], percentiles=[]).style.format(na_rep='-')

In [4]:
zipcodes_cdmx = gpd.read_file('zipcodes_cdmx.json')

In [22]:
def style_fn(feature):
    return {
        'fillColor': 'black',
        'fillOpacity': 0.0,
        'color': 'darkMagenta',
        'weight': 0.3}

def highlight_fn(feature):
    return {
        #'fillColor': ('green' if "e" in feature["properties"]["name"].lower() else "#ffff00"),
        'fillColor': 'darkMagenta',
        'fillOpacity': 0.2
    }

zipcodes_cdmx_layer = GeoJson(zipcodes_cdmx,
                              style_function=style_fn,
                              highlight_function=highlight_fn,
                              tooltip=GeoJsonTooltip(fields=["d_cp"], aliases=["CP:"]))

d, dw, dh = custom_dual_map(location=(19.35, -99.1388), tiles='cartodbpositron', zoom_start=10, submap_size=(500, 500),
                    geojson_left=zipcodes_cdmx_layer, geojson_right=None,
                    title_left='Izquierda', title_right='Derecha')

plot_dual_map(d, dw, dh)